# 3. Topic labelling

## Setup
As always, we will begin by loading a set of constants and initializing the logging system. Since we will be using Bokeh in this notebook, we will configure it to output the results in the Jupyter notebook:

In [1]:
%run __init__.py

In [2]:
from bokeh.io import output_notebook

output_notebook()

Loading BokehJS ...

In [3]:
import pandas as pd

GIT_FILE_PATH = os.path.join(NOTEBOOK_1_RESULTS_DIR, 'git_dataframe.pkl')

git_df = pd.read_pickle(GIT_FILE_PATH)
git_repositories = git_df['full_text_cleaned'].values

## Entity linking

### Using the entity linking class
An entity linking class has been defined in the _entity_linking.py_ module of the _src_ directory. This class will link the given words to their Wikidata entity by using the [wbsearchentities](https://www.wikidata.org/w/api.php?action=help&modules=wbsearchentities) modules from the MediaWiki API:

In [4]:
from herc_common.entity_linking import WikidataEntityLinker

entity_linker = WikidataEntityLinker()
res = entity_linker.link_entity('python')
res

('python', 'http://www.wikidata.org/entity/Q28865')

### Linking each topic's term to Wikidata
In the following cells we are going to load the lda model trained on the Agriculture dataset, obtain the term distribution of each topic, and link each term to Wikidata. We will start by loading both the LDA pipeline and the document term matrix with the term frequency: 

In [5]:
from herc_common.utils import load_object

lda_agriculture_pipe_filename = "git_nmf_model.pkl"
dtm_tf_filename = "git_dtm_tfidf.pkl"

lda_pipe = load_object(os.path.join(NOTEBOOK_2_RESULTS_DIR, lda_agriculture_pipe_filename))
dtm_tf = load_object(os.path.join(NOTEBOOK_2_RESULTS_DIR, dtm_tf_filename))

In order to obtain the list of terms for each topic, we are going to make use of the _get\_topic\_terms\_by\_relevance_ function to obtain a list of more relevant terms for each topic (see [Sievert & Shirley](https://nlp.stanford.edu/events/illvi2014/papers/sievert-illvi2014.pdf) for more information).

In [6]:
from herc_common.utils import get_topic_terms_by_relevance

def link_topic_terms(entity_linker, model, vectorizer,
                     dtm_tf, n_top_words, lambda_=0.6):
    res = []
    if lambda_ < 1.0:
        topic_terms = get_topic_terms_by_relevance(model, vectorizer, dtm_tf,
                                                   n_top_words, lambda_)
    else:
        feature_names = vectorizer.get_feature_names()
        topic_terms = [[feature_names[i] for i in topic.argsort()[:-n_top_words - 1: -1]] 
                       for topic in model.components_]
    return [[entity_linker.link_entity(entity) for entity in topic]
            for topic in topic_terms]


Finally, we can make used of the function defined above to link each term to Wikidata. The output of the following cell will be a 2D array, with the first dimension corresponding to each topic, and the second one consisting on tuples containing the pair ('term', 'wikidata_uri') for every term of the topic:

In [7]:
linked_terms = link_topic_terms(entity_linker, lda_pipe.named_steps['model'],
                                lda_pipe.named_steps['vectorizer'], dtm_tf, 
                                n_top_words=10, lambda_=1)
linked_terms

[[('base', 'http://www.wikidata.org/entity/Q191360'),
  ('array', 'http://www.wikidata.org/entity/Q186152'),
  ('create', 'http://www.wikidata.org/entity/Q4953270'),
  ('core', 'http://www.wikidata.org/entity/Q23595'),
  ('Index', 'http://www.wikidata.org/entity/Q873506'),
  ('Operation', 'http://www.wikidata.org/entity/Q1079196'),
  ('dialog', 'http://www.wikidata.org/entity/Q131395'),
  ('property', 'http://www.wikidata.org/entity/Q1400881'),
  ('map', 'http://www.wikidata.org/entity/Q4006'),
  ('Exporter', 'http://www.wikidata.org/entity/Q73090528')],
 [('Property', 'http://www.wikidata.org/entity/Q1400881'),
  ('spec', 'http://www.wikidata.org/entity/Q2101564'),
  ('Elda', 'http://www.wikidata.org/entity/Q608985'),
  ('Utils', 'http://www.wikidata.org/entity/Q95958203'),
  ('Renderer', None),
  ('Query', 'http://www.wikidata.org/entity/Q11169'),
  ('apispec', None),
  ('Player', 'http://www.wikidata.org/entity/Q937857'),
  ('min', 'http://www.wikidata.org/entity/Q7727'),
  ('Contex

## Obtaining each topic's graphs
In this phase we are going to explore the neighbourhood of each term linked before, to obtain a graph with their related terms from Wikidata. Each set of terms obtained before will be the seed concepts used to obtain the final graph, and a set of properties from Wikidata will be explored recursively to expand the final graph. 

For more information about the implementation of the graph building process, the class used can be accessed at the _graph.py_ module in the source directory.

In the following cell we will be configuring the graph builder to build a graph with a maxium depth of two from every seed node. Higher depth values might cause the resulting topic labels to be very general, while with a smaller value we have the risk of not obtaining a connection between the seed nodes:

In [8]:
from herc_common.graph import WikidataGraphBuilder

graph_builder = WikidataGraphBuilder(max_hops=2)
topic_graphs = [graph_builder.build_graph(topic) for topic in linked_terms]

Now that we have obtained the neighbourhood graph of each topic, we are going to plot the results using bokeh. Each node will have a different color depending on their depth with respect to the seed nodes, which will be painted in blue. This will allow us to perform an initial exploration of these graphs:

In [9]:
from bokeh.io import show
from bokeh.layouts import gridplot

from herc_common.bokeh_utils import build_graph_plot


plots = [build_graph_plot(g, f"Topic {idx}") 
         for idx, g in enumerate(topic_graphs)]
grid = gridplot(plots, ncols=2)
show(grid)

An optimum result would be to have every seed term connected in the final graph. However, theere will be some subgraphs which are isolated from the main ones. In the following section we will be solving this issue.

## Getting the main connected subgraph
As we have described before, some of the topic graphs that we have obtained are not fully connected. Small subgraphs which are isolated from the main subgraph will be considered as noise, and removed before the following computations.

In the following cells, we are going to retrieve the largest connected subgraph from each topic's graph, and plot the results to anaylise them:

In [10]:
from herc_common.graph import get_largest_connected_subgraph

connected_topic_subgraphs = [get_largest_connected_subgraph(g) 
                             for g in topic_graphs]

In [11]:
plots = [build_graph_plot(g, f"Largest Connected subgraph for topic {idx}") 
         for idx, g in enumerate(connected_topic_subgraphs)]
grid = gridplot(plots, ncols=2)
show(grid)

In this section we are aiming to see big graphs with the most amount of seed nodes possible. Graphs with few seed nodes from the original term distribution will tend to be less representative of the original topic.

## Obtaining the main component of each topic
Now that we have the final subgraph for each topic, we will be applying several centrality measures to obtain the node that best represents the topic. In the following cell we have defined an auxiliary function that receives a list of algorithm and returns the results of applying them to obtain the best _n_ entities that represent each topic:

In [12]:
import networkx.algorithms as nxa

from herc_common.graph import get_centrality_algorithm_results

def try_centrality_algorithms(topic_subgraphs, algorithms, stop_uris, top_n=4):
    markdown = ""
    for (algorithm, name) in algorithms:
        print(f'Algorithm: {name}')
        results = [get_centrality_algorithm_results(g, algorithm, stop_uris, top_n)
                   for g in topic_subgraphs]
        results_labels = [[(node[0]['label'], node[1]) for node in topic] 
                          for topic in results]
        for idx, result in enumerate(results_labels):
            print(f"Topic {idx}:", result)
            print()
        print()

        
algorithms = [
    (nxa.centrality.information_centrality, "Information centrality"),
    (nxa.centrality.eigenvector_centrality_numpy, "Eigenvector centrality"),
    (nxa.centrality.closeness_centrality, "Closeness centrality"),
    (nxa.centrality.betweenness_centrality, "Betweenness centrality"),
    (nxa.centrality.communicability_betweenness_centrality, "Communicability betweenness centrality")
]

try_centrality_algorithms(connected_topic_subgraphs,
               algorithms,
               ['Q4167836', 'Q11862829'])

Algorithm: Information centrality
Topic 0: [('map', 0.0030716084118354667), ('type of map', 0.00286892732204285), ('cartographic material', 0.0028388206059795904), ('cartographic work', 0.0028279062448461397)]

Topic 1: [('minute', 0.03928089678589703), ('hour', 0.03792607895091392), ('second', 0.037758204417419304), ('unit of time', 0.03627888993899819)]

Topic 2: [('concept', 0.015957446808510654), ('mathematical concept', 0.015228426395939089), ('axiom', 0.013392857142857144), ('abstract object', 0.013392857142857139)]

Topic 3: [('abstract object', 0.0035540722636019386), ('object', 0.0035165777492774204), ('product', 0.0034558145465768235), ('textile', 0.003374190510044103)]

Topic 4: [('protein', 0.02352941176470588), ('Probable ABC transporter ATP-binding protein MlaF/Mkl', 0.015686274509803918), ('first-order metaclass', 0.015686274509803918), ('protein family', 0.014814814814814812)]

Topic 5: [('DNA', 0.009435336266224658), ('nucleic acid', 0.008457930852327593), ('polynucleo

Topic 0: [('database', 0.6523977462419074), ('index', 0.27525590489962254), ('work', 0.2171137265964696), ('collection', 0.2145687820373118)]

Topic 1: [('minute', 0.46108526682768375), ('hour', 0.4095028802693826), ('second', 0.3616872841865819), ('unit of time', 0.3366388090995064)]

Topic 2: [('variable-order metaclass', 0.5275526639437641), ('concept', 0.5094105705080689), ('abstract object', 0.4206407289053475), ('mathematical concept', 0.219951980384907)]

Topic 3: [('textile', 0.5361289151611236), ('clothing', 0.37663471476262206), ('artificial physical object', 0.34511935504224495), ('artificial entity', 0.29262925206990453)]

Topic 4: [('protein', 0.7048830810703125), ('Probable ABC transporter ATP-binding protein MlaF/Mkl', 0.1341795427979713), ('first-order metaclass', 0.1341795427979713), ('amino acid', 0.12429850169690303)]

Topic 5: [('DNA', 0.523799424145078), ('nucleotides', 0.331306021362576), ('nucleic acid', 0.26388135589943545), ('polynucleotide', 0.2622650713183717

Topic 0: [('map', 0.23711340206185566), ('cartographic work', 0.22384428223844283), ('type of map', 0.22384428223844283), ('work', 0.21800947867298578)]

Topic 1: [('minute', 0.5897435897435898), ('second', 0.5476190476190477), ('time interval', 0.5111111111111111), ('hour', 0.5111111111111111)]

Topic 2: [('concept', 0.4307692307692308), ('mathematical concept', 0.4117647058823529), ('axiom', 0.36363636363636365), ('abstract object', 0.3373493975903614)]

Topic 3: [('abstract object', 0.23870967741935484), ('object', 0.2364217252396166), ('product', 0.23270440251572327), ('textile', 0.2276923076923077)]

Topic 4: [('protein', 0.7755102040816326), ('Probable ABC transporter ATP-binding protein MlaF/Mkl', 0.5135135135135135), ('first-order metaclass', 0.5135135135135135), ('polyamide', 0.4418604651162791)]

Topic 5: [('DNA', 0.5662650602409639), ('nucleotides', 0.44549763033175355), ('polynucleotide', 0.4392523364485981), ('nucleic acid', 0.4253393665158371)]

Topic 6: [('Generalizabili

Topic 0: [('map', 0.608337314859054), ('type of map', 0.5011944577161969), ('work', 0.464405160057334), ('first-order metaclass', 0.43645484949832775)]

Topic 1: [('second', 0.47524938829286656), ('minute', 0.33088650479954834), ('time interval', 0.27667984189723316), ('hour', 0.24788255223037828)]

Topic 2: [('concept', 0.7142857142857142), ('mathematical concept', 0.5634920634920635), ('axiom', 0.5132275132275133), ('axiomatic system', 0.2698412698412698)]

Topic 3: [('textile', 0.644144144144144), ('abstract object', 0.5879303961495742), ('object', 0.5053683820807109), ('product', 0.503517215845983)]

Topic 4: [('protein', 0.9608819345661451), ('protein family', 0.2496443812233286), ('Probable ABC transporter ATP-binding protein MlaF/Mkl', 0.13229018492176386), ('first-order metaclass', 0.13229018492176386)]

Topic 5: [('DNA', 0.7461469534050177), ('nucleotides', 0.3129718599862732), ('mitochondrion', 0.16591931670860996), ('genome', 0.15438496148859904)]

Topic 6: [('Generalizabili

Topic 0: [('map', 0.615062985423239), ('type of map', 0.5051210480224867), ('work', 0.4661800986402719), ('first-order metaclass', 0.4447677436596028)]

Topic 1: [('minute', 0.563957885480108), ('second', 0.5598284998845623), ('hour', 0.4553687938029854), ('time interval', 0.4110796494181061)]

Topic 2: [('concept', 0.7367868927067245), ('mathematical concept', 0.5799596414035302), ('axiom', 0.5233039176686631), ('axiomatic system', 0.27905910184886706)]

Topic 3: [('textile', 0.6572223823110261), ('abstract object', 0.6004877340034696), ('product', 0.5099750501409359), ('object', 0.5085349190701691)]

Topic 4: [('protein', 0.9666605734608571), ('protein family', 0.25774250620292954), ('first-order metaclass', 0.18736586167162358), ('Probable ABC transporter ATP-binding protein MlaF/Mkl', 0.18736586167162342)]

Topic 5: [('DNA', 0.8524274823423242), ('nucleotides', 0.4176593117931271), ('polynucleotide', 0.2817988474447526), ('nucleic acid', 0.25583902755838106)]

Topic 6: [('Generaliz

## Add labels to LDA model
Finally, we will be saving the best results to our LDA model that has been trained previously. Now, when we load the model again, after a topic has been inferred for a given text we will also be able to return a representative label for the topic, which will be also linked to Wikidata:

In [13]:
from herc_common.topic import Topic

final_results = [get_centrality_algorithm_results(g,
                                                 nxa.centrality.information_centrality,
                                                ['Q4167836', 'Q11862829'], top_n=1)
                 for g in connected_topic_subgraphs]

final_results_topics = [Topic.from_node(topic[0], topic[1], "lda") 
                        for result in final_results for topic in result]
lda_model = lda_pipe.named_steps['model']

In [14]:
from tqdm import tqdm

import en_core_web_md
import string
import numpy as np

en_core_web_md.load()

In [15]:
from herc_common.topic import LabelledTopicModel

labelled_topic_model = LabelledTopicModel(lda_model, final_results_topics)

lda_pipe.steps.pop()
lda_pipe.steps.append(('model', labelled_topic_model))

In [16]:
from herc_common.utils import save_object

save_object(lda_pipe, os.path.join(NOTEBOOK_3_RESULTS_DIR, 'lda_pipe_with_labels.pkl'))

## Obtaining the results for every article in the dataset

In [17]:
import en_core_sci_lg

en_core_sci_lg.load()

In [18]:
results = lda_pipe.transform(git_repositories)

## Saving the results

In [20]:
NEW_COL_NAME = 'topics_from_lda'

git_df[NEW_COL_NAME] = ['\n'.join([f"{str(topic)}, {topic.score:.5f}" for topic in result])
                        for result in results]

results_df = git_df[['gh_id', 'name', NEW_COL_NAME]]
results_df.head()

gh_id                   name  \
0  216602979                LIRICAL   
1  199330464   wikidata_ontomatcher   
2  253207181          ro-crate-ruby   
3  212556220  Misc_Training_scripts   
4  155879756              FAIRifier   

                                     topics_from_lda  
0  Protein kinase domain, 0.03182\ntextile, 0.000...  
1  Wikidata, 0.06549\ngoods, 0.00000\neducational...  
2  information, 0.07154\ntextile, 0.00000\ndocume...  
3  virtuoso, 0.17386\nlibrary science, 0.00000\nc...  
4  archaeological find, 0.13087\nmap, 0.03841\nen...

In [21]:
OUTPUT_FILE_NAME = "git_df_with_lda_topics.csv"

results_df.to_csv(os.path.join(NOTEBOOK_3_RESULTS_DIR, OUTPUT_FILE_NAME), index=False)

In [22]:
results_df

gh_id                                  name  \
0   216602979                               LIRICAL   
1   199330464                  wikidata_ontomatcher   
2   253207181                         ro-crate-ruby   
3   212556220                 Misc_Training_scripts   
4   155879756                             FAIRifier   
5    90349931                                  elda   
6   126633812            music-genre-classification   
7   173520377                     probabilistic_nlg   
8   103798851         DataStructures-Algorithms-InC   
9   153249816  Music-Generation-Using-Deep-Learning   
10  170129937                             evaluomeR   
11   57412597                          hemodonacion   
12   46532803                           DnaCompress   
13   95547920                      trackhub-creator   
14   94098106                               libpogo   
15   83849237                                 vimrc   
16   83414669                        cpp-playground   
17   56680034                          genenetwork2   
18  231038084                                  MPCC   
19   14387064                         pubannotation   
20  212904362                               UniMath   
21  113264497                     neo4j-to-reasoner   
22  260889871                           dl-reasoner   
23  161862375                             biohack18   
24  171842501                      biosample_jsonld   
25  257154635                     bh20-seq-resource   
26  260966843                                  odgi   
27  257545116                               arvados   
28  150747903                       termite_toolkit   
29  151696606                    JavaTermiteStarter   
30  126086017                               cwltool   
31  150911020                          cwl-tes-temp   
32   83817036                              mmtf-cpp   
33  254755549    covid-19-Annotations-on-Structures   
34    3103186                               php-lib   
35    3103225                       bio2rdf-scripts   
36   22713247                                  aida   
37   21820701                             memetools   
38   34799405                                owlapi   
39   42526998                  pythonontologysearch   
40  238953196                         my-react-form   
41  157134523            python-ecology-lesson-es-1   
42  193684604                        opengovernment   
43   33901216                       bioscholar-v1.0   
44   13978110                           ProvToolbox   
45  258719463                         x-spreadsheet   
46  113915480          expert-pancake-aspnetcoreapp   
47  223272173                      generalizability   
48  248895581             Data-Science--Cheat-Sheet   
49  223627473                  Basketball_Analytics   

                                      topics_from_lda  
0   Protein kinase domain, 0.03182\ntextile, 0.000...  
1   Wikidata, 0.06549\ngoods, 0.00000\neducational...  
2   information, 0.07154\ntextile, 0.00000\ndocume...  
3   virtuoso, 0.17386\nlibrary science, 0.00000\nc...  
4   archaeological find, 0.13087\nmap, 0.03841\nen...  
5      minute, 0.42500\ngoods, 0.00000\nwork, 0.00000  
6   music, 0.10166\nfirst-order metaclass, 0.03619...  
7   cosmology, 0.04792\ninformation, 0.00000\nmath...  
8   computer science, 0.12205\nwork, 0.00000\nenti...  
9   music, 0.02836\ncomputer science, 0.00000\nent...  
10   quality, 0.06077\nwork, 0.00000\nentity, 0.00000  
11  codon, 0.17930\nprotein, 0.00000\npipeline tra...  
12  DNA, 0.02316\nUtility library for structural b...  
13  pipeline transport, 0.27059\nwork, 0.00000\nwo...  
14  library science, 0.04907\nlibrary science, 0.0...  
15  software, 0.05114\nUtility library for structu...  
16  mathematics, 0.03697\ninformation, 0.00000\nma...  
17  jQuery, 0.14280\nminute, 0.00004\nminute, 0.00001  
18  Dow Jones Industrial Average, 0.03043\nprotein...  
19  HyperText Markup Language, 0.03168\nGeneraliza...  
20  function, 0.07644\nfun